In [0]:
from pyspark.sql import SparkSession
spark = SparkSession.builder.getOrCreate()

In [0]:
dbutils.fs.mount(
    source="s3a://aws-orders",
    mount_point="/mnt/bucket",
    extra_configs={"fs.s3a.access.key": ACCESS_KEY, "fs.s3a.secret.key": SECRET_KEY}
)

In [0]:
from delta.tables import *
DeltaTable.create(spark)\
    .tableName("employee_demo")\
    .addColumn("emp_id","INT")\
    .addColumn("emp_name","STRING")\
    .addColumn("gender","STRING")\
    .addColumn("salary","INT")\
    .location("dbfs:/mnt/bucket/delta/createtable").execute()
        

Out[58]: <delta.tables.DeltaTable at 0x7f665d38b9a0>

In [0]:
%sql
select * from employee_demo

emp_id emp_name gender salary

In [0]:

%fs
ls /mnt/bucket

path name size modificationTime dbfs:/mnt/bucket/athenaquery/ athenaquery/ 0 0 dbfs:/mnt/bucket/hello.png hello.png 22 1686666511000 dbfs:/mnt/bucket/mounts3databricks/ mounts3databricks/ 0 0 dbfs:/mnt/bucket/originalsales/ originalsales/ 0 0 dbfs:/mnt/bucket/raw/ raw/ 0 0 dbfs:/mnt/bucket/sales/ sales/ 0 0 dbfs:/mnt/bucket/silver/ silver/ 0 0

In [0]:
data = spark.read.format('csv')\
    .option('header',True).load("dbfs:/mnt/bucket/mounts3databricks/fake_users.csv")
display(data)

Name Email Phone Country City Zipcode Sarah Ward henry02@example.org 250-782-7727x82685 Peru East Victor 70000 Brooke Smith michael62@example.net 461.259.1003 New Zealand Davidchester 95551 Alexandria Brown DVM vmartinez@example.com +1-542-736-0748x395 Guyana East Stephaniebury 35756 David Lopez james34@example.org (206)716-4060 Suriname North Aaron 02263 Darlene Jones gregory68@example.org 001-493-632-3377x301 Lesotho North Megan 38768 John Moore jessicahill@example.org 001-806-778-2424x64905 Isle of Man East Karen 88497 Daryl Bates DDS qking@example.net (426)930-9083 Antigua and Barbuda Wheelerville 87496 George Stephenson connie51@example.net 359.717.9065 Gibraltar Christinebury 81049 Charles Vega chad12@example.net +1-765-474-9863x698 Gabon Josephchester 83754 Deborah Martin maurice99@example.org (335)569-6329x634 Egypt Rachelstad 25542 Amanda Frazier ygutierrez@example.net +1-326-345-8177x642 Cuba Larryborough 00715 Charles Obrien joseph06@example.org 289.457.6980 Ukraine Port Sheilaport 85383 Caleb Huang youngalan@example.net (640)265-3574 Botswana North Jamie 46736 Sarah Chavez meyerssydney@example.org 001-779-900-9541x22153 New Caledonia Ortizhaven 58914 Michael Holder pwebb@example.com 001-957-239-0053x906 Taiwan Lake Joelton 25816 Lisa Rodriguez ebonysimon@example.org 6005842047 Lesotho Johnathanshire 22423 Marissa Becker masonjamie@example.org (973)687-7402x9236 Philippines Rosstown 35760 William Contreras mark82@example.org 896.536.5391x60084 Kenya Littletown 67797 Erica Smith james05@example.net 5688850723 Uruguay New Marieside 98935 Michael King julia01@example.net 5626116566 British Indian Ocean Territory (Chagos Archipelago) Chandlermouth 53001 Lisa Ruiz cookheather@example.org +1-640-749-1834x4055 El Salvador Smithshire 97577 Richard Larson johnsonjonathan@example.net 9937167883 Moldova North Johnfurt 76587 Amy Deleon melinda57@example.com (989)725-2159x755 Togo Huntbury 89322 Adam Jensen mariawilson@example.net (299)910-5315x032 Korea West Melissa 88673 Cynthia Sutton richard36@example.com +1-578-261-7489x7126 British Indian Ocean Territory (Chagos Archipelago) Goodwinmouth 18436 Douglas Holland robert10@example.org 257-704-9796x0637 Malta Jacobmouth 05982 Connor Shaw ogreer@example.org 368.365.9770x246 Antarctica (the territory South of 60 deg S) East Ricky 03051 Heather Fisher walkerkathryn@example.com 411.798.8983 Comoros West Stacytown 91788 Michelle Jensen joseph66@example.com 845.881.9538 Burundi Cynthiahaven 66724 Anthony Nolan cbrown@example.org 6907068958 Faroe Islands Johnmouth 23338 Sydney Smith christina31@example.net 238.515.2257x6350 South Africa West Jason 33727 Emma Tanner doylekaren@example.net 4298230862 Australia Andrewsside 54426 Tara Jacobs donald04@example.org 001-626-372-5259x9338 Dominica North Sharon 97854 Lawrence Gardner MD timothywalsh@example.com 441-246-7571x1038 Azerbaijan East Ashleyport 08589 Hailey Price gtapia@example.org 7092320945 Honduras Port John 09904 Tammy Williams lucaschristensen@example.net (933)587-5761 Croatia Ramirezville 74509 David Buckley nicholasharris@example.org 999.853.4782 Pitcairn Islands South Ericabury 94968 Joshua Pennington john14@example.org 001-490-459-6679x67251 Thailand West Hannahland 35914 Ashley Mcgee emily57@example.com (507)445-3683x091 Italy Douglasshire 59107 Matthew Glover zmcclure@example.net 001-430-405-5590x27722 Togo Robertberg 32191 Ronald Marshall bailey00@example.net 963-511-9999 Korea Sparksmouth 55580 William Sellers kimberlysantiago@example.net 447-933-4546x48484 Botswana New Richardview 19949 Toni Ramirez samuel10@example.com (866)971-0801x6356 Gambia Port Ashley 13683 Laura Warren wilsonsara@example.org (325)351-5180x84487 Germany Gutierrezberg 62427 Jessica Johnson stephaniebutler@example.com 226.409.2288 Hong Kong East Tyler 65153 Brandon Malone gabriel96@example.net 587.278.4397 Kiribati Sarahton 98975 Claudia Mata neil50@example.com 841.362.3728 Svalbard & Jan Mayen Islands South Josephshire 28899 Brenda Ward tuckerkristi

In [0]:
print(data.count())

1000000


In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import row_number,lit

In [0]:
windowSpec = Window.partitionBy('country').orderBy('name')
outDf = data.withColumn('row_number',row_number().over(windowSpec))
display(outDf)

Name Email Phone Country City Zipcode row_number Aaron Campbell hayneskim@example.net 3348753176 Anguilla East Crystal 97082 1 Aaron Coleman clintonpollard@example.com 614-250-7732x53494 Anguilla South Danielburgh 77800 2 Aaron Diaz sarahpowell@example.net (314)321-4800x39503 Anguilla South Davidbury 77727 3 Aaron Fleming wcallahan@example.org +1-828-883-7017x80511 Anguilla New Charlesbury 49428 4 Aaron Fletcher ryan03@example.com 3724483115 Anguilla Staceyview 62758 5 Aaron Garrison kennethwilliams@example.com 001-831-402-1620x77708 Anguilla Lake Annashire 84127 6 Aaron Green krobinson@example.net +1-214-352-9285x8040 Anguilla East Marcus 57949 7 Aaron Lawson karenmcdaniel@example.net 305-235-7342x9392 Anguilla East Amy 31589 8 Aaron Lewis tonylutz@example.net (529)964-9651x3596 Anguilla Alexandriaport 21942 9 Aaron Marshall jeffrey94@example.com 915-679-1534x0511 Anguilla Terriborough 97133 10 Aaron Morgan jeffreyobrien@example.net 737.390.4082x13895 Anguilla Jennaview 44227 11 Aaron Payne garzamichael@example.net +1-728-869-0682x78588 Anguilla Johnsonhaven 95924 12 Aaron Perry laurensmith@example.com (686)868-6718 Anguilla North Charles 25980 13 Aaron Rodriguez alexanderjulie@example.org 715.267.5272x379 Anguilla West Hannah 87387 14 Aaron Sanders kelleykimberly@example.net 876-604-1758 Anguilla Swansontown 34183 15 Aaron Thomas ygreen@example.org +1-680-494-4754x270 Anguilla East Alexafurt 38976 16 Aaron Valentine wesley58@example.net 498.935.2802 Anguilla East Marktown 84418 17 Aaron Williams allen72@example.org (936)701-1103x198 Anguilla Nicholasberg 71050 18 Abigail Davis brendajohnson@example.net +1-954-256-2870x6968 Anguilla Hintonton 47901 19 Abigail Jackson emilystephens@example.org 001-622-375-5543x92671 Anguilla East Carolyn 24217 20 Abigail Wright michele70@example.net +1-969-569-3705x8714 Anguilla South Jenniferport 40083 21 Adam Burns raymond18@example.org 639-910-5240x543 Anguilla West Nicole 48161 22 Adam Burns adrianawalker@example.net (416)527-7897x85617 Anguilla Lake Markton 71327 23 Adam Carter ccox@example.net 708-422-9600 Anguilla Christopherton 36080 24 Adam Hill roberta88@example.org 001-743-413-7985 Anguilla Michaelview 41417 25 Adam Johnson brangel@example.net 712.837.3520 Anguilla North Dorothy 85800 26 Adam Jones johnsonlisa@example.org +1-261-630-4742x3817 Anguilla North Tiffanychester 78411 27 Adam Le elizabeth20@example.com 922-495-8572x029 Anguilla Port Tara 82328 28 Adam Marks espinozachristy@example.com +1-295-378-9611 Anguilla New Tammy 25238 29 Adam Murray gharris@example.net +1-572-500-5713x74250 Anguilla South Matthewburgh 18029 30 Adam Nelson ywalker@example.com 8692156026 Anguilla South Moniquemouth 56698 31 Adam Pham paul41@example.org 912-796-7411x628 Anguilla Michealview 12134 32 Adam Simpson christopherhicks@example.org 874-224-2680x54880 Anguilla Port Richard 86944 33 Adam Turner sdavis@example.net +1-999-602-5532x0781 Anguilla East Curtismouth 96345 34 Adam Wagner smithjoseph@example.com 630-741-7158x340 Anguilla Kristenport 96953 35 Adrian Sanchez marksanchez@example.com 988-856-8550 Anguilla Port Rhonda 54022 36 Adriana Schmitt jeffreyhunt@example.net 001-542-897-9574x90356 Anguilla Scottview 28345 37 Adrienne Colon holly88@example.net +1-749-401-8234x44066 Anguilla Fieldston 51149 38 Adrienne Contreras smithluis@example.com +1-246-499-4609x047 Anguilla New Kaylaport 05928 39 Aimee Davis gordondaniel@example.org 330.634.2138 Anguilla New Ashleyborough 13839 40 Aimee Fritz todd26@example.net 223.251.9580 Anguilla Martinezville 22787 41 Alan Lopez hrivera@example.com 268-752-1936x65367 Anguilla Kruegerland 12158 42 Alan Rios kbright@example.net +1-290-796-5004x0660 Anguilla Lake Amber 63022 43 Albert Collins kelly52@example.net 001-729-271-3624 Anguilla Brandiland 40763 44 Albert Hughes wstewart@example.com 254.765.7796x54272 Anguilla South Mindyshire 39190 45 Alec Torres oestrada@example.net 685.679.0571 Anguilla New Katieview 30085 46 Alejandro Bell wendyparker@example.net 001-

In [0]:
outDf.write.format('csv').option("header",True).save('/mnt/bucket/mounts3databricks/out1')

In [0]:
outDf.coalesce(1).write.format('csv').option("header",True).save('/mnt/bucket/mounts3databricks/out2')

In [0]:
outDf.write.partitionBy('country', 'city').parquet('/mnt/bucket/mounts3databricks/out3.parquet')
